# 프로젝트 설계

### 1. 주제

 - 행정동별 각 시간대 생활인구 수 추이를 파악하고, 이에 기반하여 시간대별 집중 방역 지역을 선정

### 2. Dataset

 - 서울시 열린 데이터 광장, '행정동별 서울 생활인구 ( 2017 ~ 2019년 3/4월 + 2020년 3월)'
 - 코로나 데이터

### 3. Plan

- 2017 ~ 2019년 3월/4월 생활인구 데이터를 비교하여 3월 대비 4월 생활인구 수가 증가하는 지역을 선정 ( + 인구 특성 파악 )
- 행정동별 생활인구 증가율이 가장 높은 시간대를 선정하여 방역 자원 집중
- 구별 확진자 증가 추이가 급격한 지역을 찾아 구의 인구 특성 파악

In [1]:
import pandas as pd
import numpy as np

## 행정동 코드 전처리

In [2]:
loc_code = pd.read_csv('dataset/LOCAL_PEOPLE_DONG_201904/code.csv', encoding='euc-kr')

In [3]:
loc_code.head()

시군구코드  법정동코드  행정동코드   시도명 시군구명     법정동명 행정동명     적용시작일     적용만료일
0  47900  40035      0  경상북도  예천군  지보면 마산리  NaN  19880423  99991231
1  47930  38022      0  경상북도  울진군  후포면 삼율리  NaN  19880423  99991231
2  47930  38023      0  경상북도  울진군  후포면 금음리  NaN  19880423  99991231
3  47940  25000      0  경상북도  울릉군      울릉읍  NaN  19880423  99991231
4  47940  25024      0  경상북도  울릉군  울릉읍 도동리  NaN  19880423  99991231

In [4]:
loc_code['시군구코드'] = loc_code['시군구코드'].astype(str)
loc_code['행정동코드'] = loc_code['행정동코드'].astype(str)
loc_code['행정동코드_'] = loc_code['시군구코드'] + loc_code['행정동코드']

In [5]:
loc_code = loc_code[loc_code['시도명'] == '서울특별시']
loc_code = loc_code[loc_code['행정동명'].isna() == False]
loc_code = loc_code[['행정동코드_', '시도명', '시군구명', '행정동명']]
loc_code['행정동명_'] = loc_code['시도명'] + ' ' + loc_code['시군구명'] + ' ' + loc_code['행정동명']
loc_code = loc_code[['시군구명', '행정동코드_', '행정동명_']]

In [6]:
loc_code = loc_code.drop_duplicates()

In [7]:
loc_code.isna().sum()

시군구명      0
행정동코드_    0
행정동명_     0
dtype: int64

In [8]:
loc_code[loc_code['시군구명']=='중구']

시군구명    행정동코드_                행정동명_
2182    중구  11140520         서울특별시 중구 소공동
2194    중구  11140540         서울특별시 중구 회현동
2202    중구  11140550          서울특별시 중구 명동
2225    중구  11140570          서울특별시 중구 필동
2237    중구  11140580         서울특별시 중구 장충동
2240    중구  11140590         서울특별시 중구 광희동
2250    중구  11140605        서울특별시 중구 을지로동
2260    중구  11140650       서울특별시 중구 신당제5동
2261    중구  11140670         서울특별시 중구 황학동
2262    중구  11140680         서울특별시 중구 중림동
36975   중구  11140615         서울특별시 중구 신당동
36978   중구  11140625         서울특별시 중구 다산동
36979   중구  11140635         서울특별시 중구 약수동
36980   중구  11140645         서울특별시 중구 청구동
36981   중구  11140665         서울특별시 중구 동화동
47135   중구  11140510      서울특별시 중구 태평로1가동
47146   중구  11140530     서울특별시 중구 남대문로5가동
47151   중구  11140560    서울특별시 중구 충무로4.5가동
47156   중구  11140600  서울특별시 중구 을지로3.4.5가동
47166   중구  11140610       서울특별시 중구 신당제1동
47169   중구  11140620       서울특별시 중구 신당제2동
47170   중구  11140630       서울특별시 중구 신당제3동
47171   중구  11140640       서울특별시 중구 신당제4동
47172   중구  11140660       서울특별시 중구 신당제6동

## 2019년 서울시 중구 소공동 3월/4월 생활인구 수 비교

In [9]:
ppl_1903 = pd.read_csv('dataset/LOCAL_PEOPLE_DONG_201903/LOCAL_PEOPLE_DONG_201903.csv')

# Fixing the error in index

col_names = ppl_1903.columns
ppl_1903 = ppl_1903.reset_index()
ppl_1903 = ppl_1903.iloc[:,:len(col_names)]
ppl_1903.columns = col_names
ppl_1903_ = ppl_1903.copy().round().astype('int64')

In [10]:
ppl_1903_.head()

기준일ID  시간대구분     행정동코드  총생활인구수  남자0세부터9세생활인구수  남자10세부터14세생활인구수  \
0  20190301      0  11170700   13407            151              103   
1  20190301      0  11650651   46327           1867              664   
2  20190301      0  11680730   20998            591              415   
3  20190301      0  11680670   11948            433              364   
4  20190301      0  11680740   16430            572              366   

   남자15세부터19세생활인구수  남자20세부터24세생활인구수  남자25세부터29세생활인구수  남자30세부터34세생활인구수  ...  \
0              291              476              755              664  ...   
1              852             1181             1692             1690  ...   
2              674              531              679              679  ...   
3              455              425              274              248  ...   
4              679              453              440              471  ...   

   여자25세부터29세생활인구수  여자30세부터34세생활인구수  여자35세부터39세생활인구수  여자40세부터44세생활인구수  \
0              680              617              688              509   
1             1743             1795             2137             1983   
2              808              662              779              690   
3              267              212              408              582   
4              462              544              761              693   

   여자45세부터49세생활인구수  여자50세부터54세생활인구수  여자55세부터59세생활인구수  여자60세부터64세생활인구수  \
0              549              359              491              524   
1             1839             1512             1749             1831   
2              845              870             1014             1116   
3              620              515              523              518   
4              881              629              710              694   

   여자65세부터69세생활인구수  여자70세이상생활인구수  
0              415          1011  
1             1591          3111  
2              752          1824  
3              408           629  
4              460          1224  

[5 rows x 32 columns]

In [11]:
# 결측치 확인

ppl_1903_.isna().sum()

기준일ID              0
시간대구분              0
행정동코드              0
총생활인구수             0
남자0세부터9세생활인구수      0
남자10세부터14세생활인구수    0
남자15세부터19세생활인구수    0
남자20세부터24세생활인구수    0
남자25세부터29세생활인구수    0
남자30세부터34세생활인구수    0
남자35세부터39세생활인구수    0
남자40세부터44세생활인구수    0
남자45세부터49세생활인구수    0
남자50세부터54세생활인구수    0
남자55세부터59세생활인구수    0
남자60세부터64세생활인구수    0
남자65세부터69세생활인구수    0
남자70세이상생활인구수       0
여자0세부터9세생활인구수      0
여자10세부터14세생활인구수    0
여자15세부터19세생활인구수    0
여자20세부터24세생활인구수    0
여자25세부터29세생활인구수    0
여자30세부터34세생활인구수    0
여자35세부터39세생활인구수    0
여자40세부터44세생활인구수    0
여자45세부터49세생활인구수    0
여자50세부터54세생활인구수    0
여자55세부터59세생활인구수    0
여자60세부터64세생활인구수    0
여자65세부터69세생활인구수    0
여자70세이상생활인구수       0
dtype: int64

In [12]:
ppl_1904 = pd.read_csv('dataset/LOCAL_PEOPLE_DONG_201904/LOCAL_PEOPLE_DONG_201904.csv')

# Fixing the error in index

col_names = ppl_1904.columns
ppl_1904 = ppl_1904.reset_index()
ppl_1904 = ppl_1904.drop('여자70세이상생활인구수', axis = 1)
ppl_1904.columns = col_names

ppl_1904_ = ppl_1904.copy().round().astype('int64')

In [13]:
ppl_1904_.head()

기준일ID  시간대구분     행정동코드  총생활인구수  남자0세부터9세생활인구수  남자10세부터14세생활인구수  \
0  20190401      0  11305555   28876            936              518   
1  20190401      0  11320511   24891            679              408   
2  20190401      0  11500550   17481            733              333   
3  20190401      0  11320513   14025            547              305   
4  20190401      0  11620775   22754            521              308   

   남자15세부터19세생활인구수  남자20세부터24세생활인구수  남자25세부터29세생활인구수  남자30세부터34세생활인구수  ...  \
0              600              709              920              860  ...   
1              586              633              776              720  ...   
2              379              370              503              756  ...   
3              406              361              423              384  ...   
4              617              693              785              854  ...   

   여자25세부터29세생활인구수  여자30세부터34세생활인구수  여자35세부터39세생활인구수  여자40세부터44세생활인구수  \
0              935              851             1044              974   
1              858              998              955              892   
2              581              783              841              771   
3              406              364              568              549   
4              791              803              778              751   

   여자45세부터49세생활인구수  여자50세부터54세생활인구수  여자55세부터59세생활인구수  여자60세부터64세생활인구수  \
0             1224             1188             1292             1122   
1             1211             1041             1114             1238   
2              691              562              762              714   
3              635              645              621              481   
4              903              906             1138              840   

   여자65세부터69세생활인구수  여자70세이상생활인구수  
0              928          2908  
1              730          2173  
2              602          1178  
3              402          1443  
4              700          1905  

[5 rows x 32 columns]

In [14]:
# 결측치 확인

ppl_1904_.isna().sum()

기준일ID              0
시간대구분              0
행정동코드              0
총생활인구수             0
남자0세부터9세생활인구수      0
남자10세부터14세생활인구수    0
남자15세부터19세생활인구수    0
남자20세부터24세생활인구수    0
남자25세부터29세생활인구수    0
남자30세부터34세생활인구수    0
남자35세부터39세생활인구수    0
남자40세부터44세생활인구수    0
남자45세부터49세생활인구수    0
남자50세부터54세생활인구수    0
남자55세부터59세생활인구수    0
남자60세부터64세생활인구수    0
남자65세부터69세생활인구수    0
남자70세이상생활인구수       0
여자0세부터9세생활인구수      0
여자10세부터14세생활인구수    0
여자15세부터19세생활인구수    0
여자20세부터24세생활인구수    0
여자25세부터29세생활인구수    0
여자30세부터34세생활인구수    0
여자35세부터39세생활인구수    0
여자40세부터44세생활인구수    0
여자45세부터49세생활인구수    0
여자50세부터54세생활인구수    0
여자55세부터59세생활인구수    0
여자60세부터64세생활인구수    0
여자65세부터69세생활인구수    0
여자70세이상생활인구수       0
dtype: int64

In [62]:
ppl_1903_tmp2 = ppl_1903_[ppl_1903_['기준일ID']==20190304][ppl_1903_['시간대구분']==19]
ppl_1904_tmp2 = ppl_1904_[ppl_1904_['기준일ID']==20190401][ppl_1904_['시간대구분']==12]

<ipython-input-62-9bbac30f7332>:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  ppl_1903_tmp2 = ppl_1903_[ppl_1903_['기준일ID']==20190304][ppl_1903_['시간대구분']==19]
<ipython-input-62-9bbac30f7332>:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  ppl_1904_tmp2 = ppl_1904_[ppl_1904_['기준일ID']==20190401][ppl_1904_['시간대구분']==12]


## 지도 시각화

In [16]:
import geopandas as gpd

In [17]:
df = gpd.read_file('dataset/map/seoul-dong.geojson')
df.head()

시    구    동     행정동코드  \
0  서울특별시  종로구  사직동  11110530   
1  서울특별시  종로구  삼청동  11110540   
2  서울특별시  종로구  부암동  11110550   
3  서울특별시  종로구  평창동  11110560   
4  서울특별시  종로구  무악동  11110570   

                                            geometry  
0  MULTIPOLYGON (((126.97689 37.57565, 126.97703 ...  
1  MULTIPOLYGON (((126.98269 37.59507, 126.98337 ...  
2  MULTIPOLYGON (((126.97585 37.59656, 126.97359 ...  
3  MULTIPOLYGON (((126.97507 37.63139, 126.97649 ...  
4  MULTIPOLYGON (((126.96067 37.58080, 126.96281 ...

In [18]:
import folium
folium.__version__

'0.10.1'

In [19]:
geo_data = 'dataset/map/seoul-dong.geojson'


# 서울시 중심부의 위도, 경도 입니다. 
center = [37.541, 126.986] # 맵이 center 에 위치하고, zoom 레벨은 11로 시작하는 맵 m을 만듭니다. 
m2 = folium.Map(location=center, zoom_start=10) # Choropleth 레이어를 만들고, 맵 m에 추가합니다. 
folium.Choropleth( geo_data=df, data=ppl_1903_tmp2, columns=('행정동코드', '총생활인구수'), key_on='feature.properties.행정동코드', fill_color='PuRd', legend_name='총생활인구수').add_to(m2)
# 맵 m을 출력합니다.
m2

In [58]:
geo_data = 'dataset/map/seoul-dong.geojson'


# 서울시 중심부의 위도, 경도 입니다. 
center = [37.541, 126.986] # 맵이 center 에 위치하고, zoom 레벨은 11로 시작하는 맵 m을 만듭니다. 
m = folium.Map(location=center, zoom_start=10) # Choropleth 레이어를 만들고, 맵 m에 추가합니다. 
folium.Choropleth( geo_data=df, data=ppl_1904_tmp2, columns=('행정동코드', '총생활인구수'), key_on='feature.properties.행정동코드', fill_color='PuRd', legend_name='총생활인구수').add_to(m)
# 맵 m을 출력합니다.

m

In [70]:
ppl_1904_0401 = ppl_1904_[ppl_1904_['기준일ID']==20190401]
ppl_1904_ev = ppl_1904_0401[(ppl_1904_0401['시간대구분']>=18) & (ppl_1904_['시간대구분']<=21)]
ppl_1904_ev_sum = ppl_1904_ev.groupby('행정동코드')['총생활인구수'].agg(sum)

<ipython-input-70-febc915a0910>:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  ppl_1904_ev = ppl_1904_0401[(ppl_1904_0401['시간대구분']>=18) & (ppl_1904_['시간대구분']<=21)]


In [73]:
ppl_1903_0304 = ppl_1903_[ppl_1903_['기준일ID']==20190304]
ppl_1903_ev = ppl_1903_0304[(ppl_1903_0304['시간대구분']>=18) & (ppl_1903_['시간대구분']<=21)]
ppl_1903_ev_sum = ppl_1903_ev.groupby('행정동코드')['총생활인구수'].agg(sum)

<ipython-input-73-58c7b8f859b3>:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  ppl_1903_ev = ppl_1903_0304[(ppl_1903_0304['시간대구분']>=18) & (ppl_1903_['시간대구분']<=21)]


In [74]:
center = [37.541, 126.986] # 맵이 center 에 위치하고, zoom 레벨은 11로 시작하는 맵 m을 만듭니다. 
m = folium.Map(location=center, zoom_start=10) # Choropleth 레이어를 만들고, 맵 m에 추가합니다. 
folium.Choropleth( geo_data=df, data=ppl_1903_ev_sum, columns=('행정동코드', '총생활인구수'), key_on='feature.properties.행정동코드', fill_color='PuRd', legend_name='총생활인구수').add_to(m)
# 맵 m을 출력합니다.

m

In [89]:
center = [37.541, 126.986] # 맵이 center 에 위치하고, zoom 레벨은 11로 시작하는 맵 m을 만듭니다. 
m = folium.Map(location=center, zoom_start=10) # Choropleth 레이어를 만들고, 맵 m에 추가합니다. 
folium.Choropleth( geo_data=df, data=maap, columns=('행정동코드', '총생활인구수'), key_on='feature.properties.행정동코드', fill_color='PuRd', legend_name='총생활인구수').add_to(m)
# 맵 m을 출력합니다.

m

<__array_function__ internals>:5: RuntimeWarning: Converting input from bool to <class 'numpy.uint8'> for compatibility.


In [87]:
maap = ppl_1903_ev_sum + 10000 < ppl_1904_ev_sum

In [84]:
ppl_1903_ev_sum

행정동코드
11110515     57832
11110530    120952
11110540     22324
11110550     53674
11110560     71125
             ...  
11740650    110444
11740660    115413
11740685    212495
11740690     29320
11740700    117110
Name: 총생활인구수, Length: 424, dtype: int64

In [82]:
ppl_1904_ev_sum

행정동코드
11110515     57797
11110530    116794
11110540     24211
11110550     56308
11110560     71504
             ...  
11740650    107409
11740660    113884
11740685    211222
11740690     28113
11740700    114572
Name: 총생활인구수, Length: 424, dtype: int64